## Рефакторинг исходной таблицы

В этой тетрадке мы немножко играем с данными андийских языков.

Данные взяты [отсюда](https://docs.google.com/spreadsheets/d/1wLwgyR_YBa5yuKg8ozN4aLbi4wvRCEYkwX1Xhnryuuw/edit#gid=0). (Предоставлены проектом *Field NLP - morpology*) 

Наша задача распарсить данные и преобразовать их в онтологию. Нужно преобразовать словарные вхождения из таблицы в формат RDF и модель Ontolex lemon. 

На питон существует rdf либа:

In [5]:
# !pip install rdflib

Defaulting to user installation because normal site-packages is not writeable
  Using cached rdflib-5.0.0-py3-none-any.whl (231 kB)
  Using cached isodate-0.6.0-py2.py3-none-any.whl (45 kB)


  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.


RDF состоит из триплов, триплы это субъект-предикат-объект. Типа что - как_связано - с_чем. В либе rdflib вся эта сложная структура переведена в pythonic way -- у нас собирается что-то вроде контейнера\списка с 3-х элементными кортежами внутри. 

Вот пример из [документации](https://rdflib.readthedocs.io/en/stable/gettingstarted.html):

```
[
    (subject0, predicate0, object0),
    (subject1, predicate1, object1),
    ...
    (subjectN, predicateN, objectN)
 ]
```

Чтобы сразу не бросаться в огонь, я просто переведу саму таблицу с андийскими данными в pandas. А уже потом этот dataframe можно будет аккуратно переводить в rdf.

С гугл таблицами мне помог вот этот [туториал](https://medium.com/analytics-vidhya/how-to-read-and-write-data-to-google-spreadsheet-using-python-ebf54d51a72c)

Но к сожалению, это работает везде кроме колаба. Видимо, колаб не умеет поднимать локальные сервера.

In [1]:
import re
import pandas as pd
from googleapiclient.discovery import build
from google_auth_oauthlib.flow import InstalledAppFlow,Flow
from google.auth.transport.requests import Request
import os
import pickle
from tqdm import tqdm

In [3]:
andi_sheet_id = "1wLwgyR_YBa5yuKg8ozN4aLbi4wvRCEYkwX1Xhnryuuw"

SCOPES = ['https://www.googleapis.com/auth/spreadsheets.readonly']

# here enter the id of your google sheet
SAMPLE_SPREADSHEET_ID_input = andi_sheet_id
SAMPLE_RANGE_NAME = 'A1:S68794'

def main():
    global values_input, service
    creds = None
    if os.path.exists('token.pickle'):
        with open('token.pickle', 'rb') as token:
            creds = pickle.load(token)
    if not creds or not creds.valid:
        if creds and creds.expired and creds.refresh_token:
            creds.refresh(Request())
        else:
            flow = InstalledAppFlow.from_client_secrets_file(
                'client_secret.json', SCOPES)  # here enter the name of your downloaded JSON file
            creds = flow.run_local_server(port=0)
        with open('token.pickle', 'wb') as token:
            pickle.dump(creds, token)

    service = build('sheets', 'v4', credentials=creds)

    # Call the Sheets API
    sheet = service.spreadsheets()
    result_input = sheet.values().get(spreadsheetId=SAMPLE_SPREADSHEET_ID_input,
                                range=SAMPLE_RANGE_NAME).execute()
    values_input = result_input.get('values', [])

    if not values_input:
        print('No data found.')

main()

df = pd.DataFrame(values_input[1:], columns=values_input[0])

RefreshError: ('invalid_grant: Bad Request', '{\n  "error": "invalid_grant",\n  "error_description": "Bad Request"\n}')

In [2]:
df = pd.read_csv("andic_dicts.csv", encoding='utf-8')

d:\python371\lib\site-packages\IPython\core\interactiveshell.py:3020: DtypeWarning: Columns (0,10,17,19) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
df.head()

lang  id_word  id_meaning  id    lemma   ipa morphology  bor  \
0  botl1242        1           1   1      а:хх  NaN        NaN  NaN   
1       NaN        2           1   2  аᴴгь/а́й  NaN        NaN  NaN   
2       NaN        2           2   3  аᴴгь/а́й  NaN        NaN  NaN   
3       NaN        2           3   4  аᴴгь/а́й  NaN        NaN  NaN   
4       NaN        2           4   5  аᴴгь/а́й  NaN        NaN  NaN   

      annotator   pos concepticon     meaning_ru  \
0  George Moroz  intj         NaN        баю-бай   
1  George Moroz  verb         NaN       сообщать   
2  George Moroz  verb         NaN      объявлять   
3  George Moroz  verb         NaN       нанимать   
4  George Moroz  verb         NaN  предупреждать   

                                          definition glottocode  \
0                                            баю-бай   botl1242   
1  понуд. от аᴴгьи; 1) сообщать, доводить до свед...   botl1242   
2  понуд. от аᴴгьи; 1) сообщать, доводить до свед...   botl1242   
3  понуд. от аᴴгьи; 1) сообщать, доводить до свед...   botl1242   
4  понуд. от аᴴгьи; 1) сообщать, доводить до свед...   botl1242   

              reference comments borrowing_source_word  \
0  Saidova, Abusov 2012      NaN                   NaN   
1  Saidova, Abusov 2012      NaN                   NaN   
2  Saidova, Abusov 2012      NaN                   NaN   
3  Saidova, Abusov 2012      NaN                   NaN   
4  Saidova, Abusov 2012      NaN                   NaN   

  borrowing_source_comment   74,52% Unnamed: 19  
0                      NaN   4473.0         NaN  
1                      NaN   9449.0         NaN  
2                      NaN  12706.0         NaN  
3                      NaN   6868.0         NaN  
4                      NaN  12724.0         NaN

Делаем кокой-то RDF (пока не знаем какой, просто делаем, чтобы знать, что мы такое умеем)

In [4]:
import rdflib
from rdflib.namespace import RDF, RDFS, OWL, DC, DCTERMS
from rdflib.term import URIRef, Literal

In [52]:
g = rdflib.Graph(identifier='http://example.org/ontolex/andi#')  # пока рандомная ссылка

In [53]:
andi = rdflib.Namespace('http://example.org/ontolex/andi#')  # Корневой Namespace с рандомной ссылкой

ontolex = rdflib.Namespace('http://www.w3.org/ns/lemon/ontolex#')  # основная модель
lexinfo = rdflib.Namespace('http://www.lexinfo.net/ontology/2.0/lexinfo#')  # обозначение морфологических тегов
lime = rdflib.Namespace('http://www.w3.org/ns/lemon/lime#')
#synsem = rdflib.Namespace('http://www.w3.org/ns/lemon/synsem#')  # синтаксис
#decomp = rdflib.Namespace('http://www.w3.org/ns/lemon/decomp#')  # синтаксис
vartrans = rdflib.Namespace('http://www.w3.org/ns/lemon/vartrans#')  # для обозначения переводов и вариантов слов
skos = rdflib.Namespace('http://www.w3.org/2004/02/skos#')

In [54]:
g.bind('ontolex', ontolex)
g.bind('lexinfo', lexinfo)
g.bind('dct', DCTERMS)  # Это для того, чтобы названия ISO языков грузились
g.bind('rdfs', RDFS)
g.bind('lime', lime)  # ??
#g.bind('synsem', synsem)
#g.bind('decomp', decomp)
g.bind('vartrans', vartrans)
g.bind('skos', skos)

g.bind('andi', andi)

lexicon_andi = URIRef(andi)

In [55]:
# Надо вот тут добавить все типы триплов, чтобы они добавились в префиксы ниже
g.set((lexicon_andi, RDF.type, lime.Lexicon))
g.set((lexicon_andi, ontolex.language, Literal("ru, ani")))
g.set((lexicon_andi, RDFS.comment, Literal("lexicon-information_name:Andi-Russian", lang="en")))

#g.set((lexicon_andi, andi, Literal("entry")))

#lime:Lexicon_Kadag1884_bbl a ontolex:Lexicon.
#lime:Lexicon_Kadag1884_bbl ontolex:language "bbl", "ka", "ru".
#lime:Lexicon_Kadag1884_bbl rdfs:comment "lexicon-information_name:Kadagidze - Batsbi-Georgian-Russian"@en.

#g.set((apics_doc, ligt.hasUtterances, apics.examples))
#g.set((apics.examples, RDF.type, ligt.InterlinearCollection))
#Probably it should also be a `dc:bibliographicCitation`
#g.set((apics.examples, RDFS.comment, Literal(apics_dataset.properties['dc:bibliographicCitation '], lang="en")))

In [9]:
# сделала пустой turtle, прикольно
print(g.serialize(format='turtle').decode('utf-8'))

@prefix andi: <http://example.org/ontolex/andi#> .
@prefix lime: <http://www.w3.org/ns/lemon/lime#> .
@prefix ontolex: <http://www.w3.org/ns/lemon/ontolex#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .

andi: a lime:Lexicon ;
    rdfs:comment "lexicon-information_name:Andi-Russian"@en ;
    ontolex:language "ru, ani" .




In [10]:
# check what POS names are used in the original table
df['pos'].value_counts().index.tolist()

['noun',
 'verb',
 'adj',
 'adv',
 'noun III',
 'noun IV',
 'masdar',
 'num',
 'noun V',
 'pron',
 'intj',
 'part',
 'x',
 'noun I',
 'post',
 'particle',
 '?',
 'noun I,II',
 'masd',
 'noun II',
 'excl',
 'expression',
 'onomatope',
 'conj',
 'participle',
 'aux',
 'adverb',
 'adv?',
 'noun?',
 'prep',
 'morph',
 'noun II,IV',
 'verb/adj',
 'adj?',
 'part?',
 'adposition',
 'noun I,II,III',
 'particle?',
 'ordinal',
 'pred',
 'pronoun',
 'verb/adv',
 'ayx',
 'verb?',
 'adposition?',
 'excl?',
 '???',
 'morpheme',
 'noun I,III',
 'num?',
 'союз',
 'gerund?',
 'noun I,I',
 'noun VI',
 '? :)',
 'masdar?',
 'expression/noun',
 'expr',
 'part, adv']

In [11]:
df['morphology'].value_counts().index.tolist()

['(-лIа)',
 'no info',
 '(-ролIи)',
 '(–лъ)',
 '4',
 '(–лъилъ)',
 '(-лIи)',
 "(-а̄ри, -ва, -айа', -айе̄гье, -а̄ре)",
 '(-лIа, -би)',
 "(-ари', -ва, -а', -е̄'гье, -е'ре)",
 '(–лъ,–би)',
 '5',
 '(-лIи, -бé)',
 '(-лIа, -аби)',
 '(-лI, -бе)',
 '(–л,–лас̄,–лá,–л̄о,–лēх)',
 '(-о, -ā, -иба, -о/-ōта, -ā)',
 '(–илъ,–аби)',
 '(-0, -с, -0, -бхва, -йдйа)',
 '(-ол|, -ди)',
 '(-л|, -ди)',
 '(–лъ,–аби)',
 '(–илъ)',
 '(-л|)',
 '(-нолIи)',
 '(-áло, -áлā, -алá, -áло/-áлōта, -áлā)',
 '(-ало, -алā, -ала, -ало/-алōта, -алā)',
 '(-áлIи)',
 '(-илI, -бе)',
 '(-лъ̄илIи)',
 '(-лъ̄илIи / -лIи, -ди)',
 '(–ø,–ас̄,–бе,–б/о,–āх)',
 '(-ол|)',
 '(-о, -ā́, -ибá, -о/-ṓта, -ā́)',
 "(-а̄'ри, -ва, -айа', -а'йе̄гье, -а̄'ре)",
 '3',
 "(-ари, -ва, -а', -е̄гье, -ере)",
 '(-лъ̄илIи / -лIи)',
 '(-о, -ā, -а, -о/-ōта, -ā)',
 '(–ø,–ас̄,–бé,–б/о,–ēх)',
 '(-е, -ас, -и, -ебхва, -идйа)',
 '(-лI, -ди)',
 '(–л,–лас̄,–ла,–л̄о,–лēх)',
 '(-ийо, -ийā, -ӣба, -ийо/-ийōта, -ийā)',
 '(-лъ̄илIи, -ди)',
 '(-илIи, -абé)',
 '(-лIи / -лъ̄илIи, -ди)'

In [57]:
for lemma in tqdm(df['lemma '][1:3800]):
    morph = df[df['lemma '] == lemma]['morphology'].values[0]
    if not pd.isna(morph) and morph.startswith("("):
        print(morph.strip("()").split(", "))

100%|█████████████████████████████████████████████████████████████████████████████| 3799/3799 [00:30<00:00, 122.88it/s]


In [56]:
for lemma in tqdm(df['lemma '][1:3800]):
    pos = df[df['lemma '] == lemma]['pos'].values[0]
    if not pd.isna(pos):
        print(pos)

  0%|                                                                                         | 0/3799 [00:00<?, ?it/s]

verb
verb
verb
verb
verb
verb
verb


  0%|▏                                                                                | 7/3799 [00:00<01:01, 62.11it/s]

verb
verb
noun
noun
noun
verb


  0%|▎                                                                               | 13/3799 [00:00<01:02, 60.66it/s]

...

 99%|█████████████████████████████████████████████████████████████████████████████▌| 3779/3799 [00:58<00:00, 82.82it/s]

verb
noun
verb


100%|█████████████████████████████████████████████████████████████████████████████▊| 3789/3799 [00:58<00:00, 86.92it/s]

verb
verb
noun
noun


100%|██████████████████████████████████████████████████████████████████████████████| 3799/3799 [00:58<00:00, 90.29it/s]


In [77]:
### m a i n ###

i = 1

for lemma in tqdm(df['lemma '][1:]):
    lemma = lemma.replace(' ', '_')
    lemma = lemma.replace('/', '_')
    lemma = lemma.replace('\\', '_')
    
    entry_num = "entry_" + str(i)
    entry_form_num = "entry_" + str(i) + "_form"
    
    # LexicalEntry
    g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), RDF.type, ontolex.LexicalEntry))
    g.add((ontolex.LexicalEntry, DCTERMS.language, URIRef('http://id.loc.gov/vocabulary/iso639-3/ani')))
    g.add((ontolex.LexicalEntry, ontolex.canonicalForm, URIRef('http://example.org/ontolex/andi/' + entry_form_num)))
    
    try:
        morph = df[df['lemma '] == lemma]['morphology'].values[0]
    except IndexError:
        morph = ''
    if not pd.isna(morph) and morph.startswith("("):
        endings = morph.strip("()").split(", ")
        for k, ending in enumerate(endings):
            # other lexicalForm
            g.add((ontolex.LexicalEntry, ontolex.lexicalForm, URIRef('http://example.org/ontolex/andi/' + entry_form_num + '_' + str(k))))
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_form_num + '_' + str(k)), RDF.type, ontolex.Form))
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_form_num + '_' + str(k)), ontolex.writtenRep, Literal(lemma + " " + ending, lang='ani')))
    
    # lexicalForm
    g.add((URIRef('http://example.org/ontolex/andi/' + entry_form_num), RDF.type, ontolex.Form))
    g.add((URIRef('http://example.org/ontolex/andi/' + entry_form_num), ontolex.writtenRep, Literal(lemma, lang='ani')))
    ipa = df[df['lemma '] == lemma]['ipa']
    if not ipa.empty:
        ipa = ipa.values[0]
        if ipa != '':
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_form_num), ontolex.phoneticRep, Literal(ipa, lang='ipa')))
    
    # у некоторых слов есть несколько переводов, это обозначено, как новые строки таблицы
    # пока чтобы не париться я беру только один перевод
    translation = df[df['lemma '] == lemma]['meaning_ru']
    if not translation.empty:
        translation = translation.values[0]
        if isinstance(translation, str):
            if ' ' in translation:
                translation = translation.replace(' ', '_')
            translation = translation.replace('/', '_')
            translation = translation.replace('\\', '_')

            ### Translation as shared reference
            #ontolex:sense :surrogate_mother_sense.
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), ontolex.sense, URIRef('http://example.org/ontolex/andi/' + 'sense_andi_' + entry_num)))

            # :surrogate_mother_sense ontolex:reference ontology:SurrogateMother.
            g.add((URIRef('http://example.org/ontolex/andi/' + 'sense_andi_' + entry_num), ontolex.reference, URIRef('http://example.org/ontolex/andi/' + translation)))

            # LexicalForm of Russian word
            g.add((URIRef('http://example.org/ontolex/andi/' + 'rus_' + entry_num), RDF.type, ontolex.LexicalEntry))
            g.add((ontolex.LexicalEntry, DCTERMS.language, URIRef('http://id.loc.gov/vocabulary/iso639-2/rus')))
            g.add((ontolex.LexicalEntry, ontolex.canonicalForm, URIRef('http://example.org/ontolex/andi/' + 'rus_' + entry_form_num)))
            g.add((URIRef('http://example.org/ontolex/andi/' + 'rus_' + entry_form_num), RDF.type, ontolex.Form))
            g.add((URIRef('http://example.org/ontolex/andi/' + 'rus_' + entry_form_num), ontolex.writtenRep, Literal(translation, lang='rus')))
            g.add((URIRef('http://example.org/ontolex/andi/' + 'rus_' + entry_num), ontolex.sense, URIRef('http://example.org/ontolex/andi/' + 'sense_rus_' + entry_num)))

            # :surrogate_mother_sense ontolex:reference ontology:SurrogateMother.
            g.add((URIRef('http://example.org/ontolex/andi/' + 'sense_rus_' + entry_num), ontolex.reference, URIRef('http://example.org/ontolex/andi/' + translation)))

    # partOfSpeech
    try:
        pos = df[df['lemma '] == lemma]['pos'].values[0]
    except IndexError:
        pos = ''
    if not pd.isna(pos):
        if re.match(r'.*?[nN]oun.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.noun))
        elif re.match(r' ?adj.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.adjective))
        elif re.match(r'.*?adv.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.adverb))
        elif re.match(r' ?verb.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.verb))
        elif re.match(r'num.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.numeral))
        elif re.match(r'.*?ord.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.indefiniteOrdinalNumeral))
        elif re.match(r' ?adp.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.adposition))
        elif re.match(r' ?gerund.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.gerundive))
        elif re.match(r'.*?participle.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.participle))
        elif re.match(r'.*?part.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.particle))
        elif re.match(r'excl.*', pos):
            g.add((URIRef('http://example.org/ontolex/andi/' + entry_num), lexinfo.partOfSpeech, lexinfo.exclamativePoint))
            
    i += 1




  0%|                                                                                        | 0/84316 [00:00<?, ?it/s]


  0%|                                                                              | 2/84316 [00:00<1:12:52, 19.28it/s]


  0%|                                                                              | 5/84316 [00:00<1:07:41, 20.76it/s]


  0%|                                                                              | 8/84316 [00:00<1:02:30, 22.48it/s]


  0%|                                                                             | 11/84316 [00:00<1:00:26, 23.25it/s]


  0%|                                                                             | 13/84316 [00:00<1:04:10, 21.90it/s]


  0%|                                                                             | 15/84316 [00:00<1:13:36, 19.09it/s]


  0%|                                                                             | 17/84316 [00:00<1:23:32, 16.82it/s]


  0%|                

  0%|▏                                                                           | 192/84316 [00:08<1:04:12, 21.84it/s]


  0%|▏                                                                           | 195/84316 [00:08<1:20:02, 17.52it/s]


  0%|▏                                                                           | 197/84316 [00:08<1:21:11, 17.27it/s]


  0%|▏                                                                           | 200/84316 [00:08<1:11:57, 19.48it/s]


  0%|▏                                                                           | 203/84316 [00:09<1:07:25, 20.79it/s]


  0%|▏                                                                           | 206/84316 [00:09<1:03:08, 22.20it/s]


  0%|▏                                                                           | 209/84316 [00:09<1:08:14, 20.54it/s]


  0%|▏                                                                           | 212/84316 [00:09<1:12:22, 19.37it/s]


  0%|▏                  

  0%|▎                                                                             | 400/84316 [00:16<52:43, 26.52it/s]


  0%|▎                                                                             | 403/84316 [00:16<51:24, 27.20it/s]


  0%|▍                                                                             | 406/84316 [00:16<51:45, 27.02it/s]


  0%|▍                                                                             | 409/84316 [00:16<52:15, 26.76it/s]


  0%|▍                                                                             | 412/84316 [00:17<54:09, 25.82it/s]


  0%|▍                                                                             | 415/84316 [00:17<52:16, 26.75it/s]


  0%|▍                                                                             | 418/84316 [00:17<50:57, 27.44it/s]


  0%|▍                                                                             | 421/84316 [00:17<54:41, 25.56it/s]


  1%|▍                  

  1%|▌                                                                             | 606/84316 [00:24<51:47, 26.94it/s]


  1%|▌                                                                             | 610/84316 [00:24<49:36, 28.12it/s]


  1%|▌                                                                             | 613/84316 [00:24<59:56, 23.27it/s]


  1%|▌                                                                           | 616/84316 [00:25<1:04:38, 21.58it/s]


  1%|▌                                                                           | 619/84316 [00:25<1:00:24, 23.09it/s]


  1%|▌                                                                             | 622/84316 [00:25<59:07, 23.59it/s]


  1%|▌                                                                             | 625/84316 [00:25<56:32, 24.67it/s]


  1%|▌                                                                           | 628/84316 [00:25<1:01:16, 22.76it/s]


  1%|▌                  

  1%|▊                                                                             | 811/84316 [00:32<47:01, 29.59it/s]


  1%|▊                                                                             | 815/84316 [00:32<46:39, 29.83it/s]


  1%|▊                                                                             | 819/84316 [00:33<45:40, 30.47it/s]


  1%|▊                                                                             | 823/84316 [00:33<48:13, 28.85it/s]


  1%|▊                                                                             | 826/84316 [00:33<50:05, 27.78it/s]


  1%|▊                                                                             | 829/84316 [00:33<49:37, 28.04it/s]


  1%|▊                                                                             | 832/84316 [00:33<48:45, 28.54it/s]


  1%|▊                                                                             | 836/84316 [00:33<47:39, 29.19it/s]


  1%|▊                  

...

 99%|███████████████████████████████████████████████████████████████████████████▏| 83449/84316 [53:25<00:32, 26.87it/s]


 99%|███████████████████████████████████████████████████████████████████████████▏| 83452/84316 [53:25<00:31, 27.54it/s]


 99%|███████████████████████████████████████████████████████████████████████████▏| 83455/84316 [53:25<00:30, 27.78it/s]


 99%|███████████████████████████████████████████████████████████████████████████▏| 83458/84316 [53:25<00:31, 27.32it/s]


 99%|███████████████████████████████████████████████████████████████████████████▏| 83461/84316 [53:25<00:31, 27.18it/s]


 99%|███████████████████████████████████████████████████████████████████████████▏| 83464/84316 [53:25<00:31, 27.45it/s]


 99%|███████████████████████████████████████████████████████████████████████████▏| 83467/84316 [53:25<00:30, 27.39it/s]


 99%|███████████████████████████████████████████████████████████████████████████▏| 83470/84316 [53:26<00:30, 27.34it/s]


 99%|███████████████████

 99%|███████████████████████████████████████████████████████████████████████████▍| 83638/84316 [53:32<00:24, 27.52it/s]http://example.org/ontolex/andi/см._рел|ан does not look like a valid URI, trying to serialize this will break.
http://example.org/ontolex/andi/см._рел|ан does not look like a valid URI, trying to serialize this will break.



 99%|███████████████████████████████████████████████████████████████████████████▍| 83641/84316 [53:32<00:25, 26.63it/s]


 99%|███████████████████████████████████████████████████████████████████████████▍| 83644/84316 [53:32<00:24, 27.43it/s]


 99%|███████████████████████████████████████████████████████████████████████████▍| 83647/84316 [53:32<00:24, 27.78it/s]


 99%|███████████████████████████████████████████████████████████████████████████▍| 83650/84316 [53:32<00:23, 27.80it/s]


 99%|███████████████████████████████████████████████████████████████████████████▍| 83653/84316 [53:32<00:24, 27.51it/s]


 99%|███████████████████████████████████████

 99%|███████████████████████████████████████████████████████████████████████████▌| 83827/84316 [53:39<00:17, 28.09it/s]


 99%|███████████████████████████████████████████████████████████████████████████▌| 83830/84316 [53:39<00:17, 28.02it/s]


 99%|███████████████████████████████████████████████████████████████████████████▌| 83833/84316 [53:39<00:17, 28.12it/s]


 99%|███████████████████████████████████████████████████████████████████████████▌| 83836/84316 [53:39<00:17, 27.66it/s]


 99%|███████████████████████████████████████████████████████████████████████████▌| 83839/84316 [53:39<00:17, 27.79it/s]http://example.org/ontolex/andi/см_гье-делъй-бик|у does not look like a valid URI, trying to serialize this will break.
http://example.org/ontolex/andi/см_гье-делъй-бик|у does not look like a valid URI, trying to serialize this will break.
http://example.org/ontolex/andi/см._гьеме-бик|убарел does not look like a valid URI, trying to serialize this will break.
http://example.org/ontolex/andi

http://example.org/ontolex/andi/{тук.)_см._—_гвала does not look like a valid URI, trying to serialize this will break.



100%|███████████████████████████████████████████████████████████████████████████▋| 84002/84316 [53:45<00:11, 26.90it/s]


100%|███████████████████████████████████████████████████████████████████████████▋| 84005/84316 [53:45<00:11, 27.40it/s]


100%|███████████████████████████████████████████████████████████████████████████▋| 84008/84316 [53:45<00:11, 27.61it/s]


100%|███████████████████████████████████████████████████████████████████████████▋| 84011/84316 [53:45<00:11, 27.38it/s]


100%|███████████████████████████████████████████████████████████████████████████▋| 84015/84316 [53:45<00:10, 28.10it/s]


100%|███████████████████████████████████████████████████████████████████████████▋| 84018/84316 [53:45<00:10, 27.87it/s]http://example.org/ontolex/andi/см._ц|ай,_балъалъа does not look like a valid URI, trying to serialize this will break.
http://example.org/ontolex/a

100%|███████████████████████████████████████████████████████████████████████████▉| 84190/84316 [53:52<00:05, 22.89it/s]


100%|███████████████████████████████████████████████████████████████████████████▉| 84193/84316 [53:52<00:05, 22.91it/s]


100%|███████████████████████████████████████████████████████████████████████████▉| 84196/84316 [53:52<00:05, 23.52it/s]


100%|███████████████████████████████████████████████████████████████████████████▉| 84199/84316 [53:53<00:04, 23.68it/s]


100%|███████████████████████████████████████████████████████████████████████████▉| 84202/84316 [53:53<00:04, 23.37it/s]


100%|███████████████████████████████████████████████████████████████████████████▉| 84205/84316 [53:53<00:04, 22.98it/s]


100%|███████████████████████████████████████████████████████████████████████████▉| 84208/84316 [53:53<00:04, 24.49it/s]


100%|███████████████████████████████████████████████████████████████████████████▉| 84211/84316 [53:53<00:04, 25.28it/s]


100%|███████████████████

In [69]:
print(g.serialize(format='turtle').decode('utf-8'))

@prefix andi: <http://example.org/ontolex/andi#> .
@prefix dct: <http://purl.org/dc/terms/> .
@prefix lexinfo: <http://www.lexinfo.net/ontology/2.0/lexinfo#> .
@prefix lime: <http://www.w3.org/ns/lemon/lime#> .
@prefix ontolex: <http://www.w3.org/ns/lemon/ontolex#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

andi: a lime:Lexicon ;
    rdfs:comment "lexicon-information_name:Andi-Russian"@en ;
    ontolex:language "ru, ani" .

<http://example.org/ontolex/andi/entry_1> a ontolex:LexicalEntry ;
    lexinfo:partOfSpeech lexinfo:verb ;
    ontolex:sense <http://example.org/ontolex/andi/sense_andi_entry_1> .

<http://example.org/ontolex/andi/entry_10> a ontolex:LexicalEntry ;
    lexinfo:partOfSpeech lexinfo:noun ;
    ontolex:sense <http://example.org/ontolex/andi/sense_andi_entry_10> .

<http://example.org/ontolex/andi/entry_100> a ontolex:LexicalEntry ;
    lexinfo:partOfSpeech lexinfo:noun ;
    ontolex:sense <http://exampl

In [78]:
g.serialize(destination='output_full_long.ttl', format='turtle')

Exception: "http://example.org/ontolex/andi/см._Б/ИКI’Á\М" does not look like a valid URI, I cannot serialize this as N3/Turtle. Perhaps you wanted to urlencode it?

In [ ]:
###      ###      ###
#####################
###               ###
### previous code ###
###               ###


for lemma in tqdm(df['lemma '][1:100]):
    if ' ' in lemma:
        lemma = lemma.replace(' ', '_')
        
    g.add((andi.entry_1, RDF.type, ontolex.LexicalEntry))
    g.add((ontolex.LexicalEntry, DCTERMS.language, URIRef('http://id.loc.gov/vocabulary/iso639-3/ani')))
    g.add((ontolex.LexicalEntry, ontolex.canonicalForm, andi.entry_1_form))
    g.add((andi.entry_1_form, RDF.type, ontolex.Form))
    g.add((andi.entry_1_form, ontolex.writtenRep, Literal(lemma, lang='ani')))
    
    #g.add((Literal(lemma), ontolex.sense, Literal(lemma + '_sense')))
    
    # у некоторых слов есть несколько переводов, это обозначено, как новые строки таблицы
    # пока чтобы не париться я беру только один перевод
    translation = df[df['lemma '] == lemma]['meaning_ru']
    if not translation.empty:
        translation = translation.values[0]
        if ' ' in translation:
            translation = translation.replace(' ', '_')
            
        g.add((Literal(lemma), vartrans.Translation, Literal(translation)))
        g.add((Literal(translation), vartrans.Translation, Literal(lemma)))

        g.add((Literal(translation), RDF.type, ontolex.LexicalEntry))
        g.add((Literal(translation), ontolex.LexicalForm, Literal(translation + '_form')))
        g.add((Literal(translation + '_form'), ontolex.writtenRep, Literal(translation, lang='rus')))
        g.add((Literal(translation), DCTERMS.language, URIRef('http://id.loc.gov/vocabulary/iso639-2/rus')))
        #g.add((Literal(translation), ontolex.sense, Literal(translation + '_sense')))
        
        definition = df[df['lemma '] == lemma]['definition']
        if not definition.empty:
            definition = definition.values[0]
            if definition != '':
                g.add((Literal(translation + '_lexical_concept'), RDF.type, ontolex.LexicalConcept))
                g.add((Literal(translation + '_lexical_concept'), skos.definition, Literal(definition)))
                g.add((Literal(translation + '_lexical_concept'), ontolex.isEvokedBy, Literal(lemma)))
                g.add((Literal(lemma), ontolex.evokes, Literal(translation + '_lexical_concept')))
        